In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


In [7]:
df_Helsinki = pd.read_csv("Helsinki.csv")
df_Helsinki.head()

Unnamed: 0  Postal Code                      Place Name Unnamed: 3  \
0         FI          100  Helsinki                          Uusimaa   
1         FI          120  Helsinki                          Uusimaa   
2         FI          130  Helsinki                          Uusimaa   
3         FI          140  Helsinki                          Uusimaa   
4         FI          150  Helsinki                          Uusimaa   

   Unnamed: 4   Borough  Unnamed: 6 Neighborhood  Unnamed: 8  Latitude  \
0           1  Helsinki          11     Helsinki          91   60.1714   
1           1  Helsinki          11     Helsinki          91   60.1632   
2           1  Helsinki          11     Helsinki          91   60.1645   
3           1  Helsinki          11     Helsinki          91   60.1578   
4           1  Helsinki          11     Helsinki          91   60.1570   

   Longitude  Unnamed: 11  
0    24.9316          6.0  
1    24.9391          6.0  
2    24.9487          6.0  
3    24.9525          6.0  
4    24.9369          6.0

In [8]:
# df_Helsinki=df_Helsinki[df.columns[1:7]]
df_Helsinki.drop(df_Helsinki.columns[[0,2,3,4,6,8,11]], axis = 1, inplace = True) 
# df_Seoul.columns=["Name of Location", "Latitude", "Longitude", "Feature class"]
df_Helsinki.head()

Postal Code   Borough Neighborhood  Latitude  Longitude
0          100  Helsinki     Helsinki   60.1714    24.9316
1          120  Helsinki     Helsinki   60.1632    24.9391
2          130  Helsinki     Helsinki   60.1645    24.9487
3          140  Helsinki     Helsinki   60.1578    24.9525
4          150  Helsinki     Helsinki   60.1570    24.9369

In [9]:
df_Helsinki.shape

(3117, 5)

In [10]:
address = 'Helsinki, Finland'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Helsinki are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.22.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinate of Helsinki are 60.1674098, 24.9425769.


In [11]:
# create map of New York using latitude and longitude values
map_Helsinki = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_Helsinki['Latitude'], df_Helsinki['Longitude'], df_Helsinki['Borough'], df_Helsinki['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Helsinki)  
    
map_Helsinki

In [12]:
dfnew_Helsinki = df_Helsinki[df_Helsinki['Borough'].str.contains('Helsinki')].reset_index(drop=True)
dfnew_Helsinki.head()

Postal Code   Borough Neighborhood  Latitude  Longitude
0          100  Helsinki     Helsinki   60.1714    24.9316
1          120  Helsinki     Helsinki   60.1632    24.9391
2          130  Helsinki     Helsinki   60.1645    24.9487
3          140  Helsinki     Helsinki   60.1578    24.9525
4          150  Helsinki     Helsinki   60.1570    24.9369

In [13]:
address = 'Helsinki, Finland'

geolocator = Nominatim()
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Helsinki Neighborhoods are {}, {}.'.format(latitude, longitude))

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: DeprecationWarning: Using Nominatim with the default "geopy/1.22.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.
  This is separate from the ipykernel package so we can avoid doing imports until


The geograpical coordinate of Helsinki Neighborhoods are 60.1674098, 24.9425769.


In [14]:
# create map of Helsinki using latitude and longitude values
map_HelsinkiNeigh = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(dfnew_Helsinki['Latitude'], dfnew_Helsinki['Longitude'], dfnew_Helsinki['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_HelsinkiNeigh)  
    
map_HelsinkiNeigh

In [15]:
CLIENT_ID = 'U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3' # your Foursquare ID
CLIENT_SECRET = 'P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3
CLIENT_SECRET:P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU


In [16]:
dfnew_Helsinki.loc[0, 'Neighborhood']

'Helsinki'

In [17]:
neighborhood_latitude = dfnew_Helsinki.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = dfnew_Helsinki.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = dfnew_Helsinki.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Helsinki are 60.1714, 24.9316.


## Get Top Locations 

In [18]:

LIMIT = 100 # limit of number of venues returned by Foursquare API

radius = 1000 # define radius
 # create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL


'https://api.foursquare.com/v2/venues/explore?&client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&v=20180605&ll=60.1714,24.9316&radius=1000&limit=100'

In [19]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedec8677af03001bdb854a'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Etu-Töölö',
  'headerFullLocation': 'Etu-Töölö, Helsinki',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 217,
  'suggestedBounds': {'ne': {'lat': 60.18040000900001,
    'lng': 24.949660067374843},
   'sw': {'lat': 60.16239999099999, 'lng': 24.913539932625156}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4adcdb23f964a520dc6021e3',
       'name': 'Taidehalli',
       'location': {'address': 'Nervanderinkatu 3',
        'lat': 60.172127213487165,
        'lng': 24.93101423081712,
        'labeledLatLngs': [{'label': 'display',
          'lat': 60.172

In [20]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [21]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name                 categories        lat  \
0                           Taidehalli                Art Gallery  60.172127   
1                         Ateljé Finne    Scandinavian Restaurant  60.171198   
2                                Baana                       Road  60.169973   
3               Twisted Street Kitchen           Asian Restaurant  60.170641   
4                                Pobre        Filipino Restaurant  60.169500   
5    Arkadia Oy International Bookshop                  Bookstore  60.173369   
6                          Ruohonjuuri          Health Food Store  60.170016   
7                           Cafe Rouge  Middle Eastern Restaurant  60.168711   
8                               Kiasma                 Art Museum  60.171652   
9                             Amos Rex                 Art Museum  60.170643   
10           Luonnontieteellinen museo             Science Museum  60.171350   
11                      Tortilla House              Burrito Place  60.169136   
12                                Alko                  Wine Shop  60.170760   
13                                Hoku        Hawaiian Restaurant  60.169490   
14                       Lautapelit.fi           Toy / Game Store  60.169471   
15                                 HAM                 Art Museum  60.169792   
16                     Polarn O. Pyret                 Kids Store  60.169473   
17                            Futurice                IT Services  60.168766   
18                     La Torrefazione                       Café  60.170721   
19                        Musiikkitalo               Concert Hall  60.173424   
20                        Young Hearts                 Restaurant  60.171353   
21             Plaza Wine & Craft Beer                   Wine Bar  60.169200   
22        Helsingin Astanga joogakoulu                Yoga Studio  60.168128   
23                              Fafa's         Falafel Restaurant  60.169876   
24                      Kaffecentralen                Coffee Shop  60.167580   
25                              Sandro  Middle Eastern Restaurant  60.169640   
26               Keltainen Jäänsärkijä                Record Shop  60.168564   
27                       Temppeliaukio                      Plaza  60.172552   
28                                  6k                 Food Court  60.169213   
29                    Fisken på Disken         Seafood Restaurant  60.169432   
30                       ELIXIA Kamppi       Gym / Fitness Center  60.169483   
31                   Singapore Hot Wok           Malay Restaurant  60.169163   
32                         Kino Regina        Indie Movie Theater  60.173869   
33                           The Ounce                   Tea Room  60.167182   
34                           Cafetoria                Coffee Shop  60.173203   
35                   New Bamboo Center         Chinese Restaurant  60.167940   
36               Kissakahvila Helkatti                   Pet Café  60.167274   
37                               Orion        Indie Movie Theater  60.166393   
38                Navy Jerry's Rum Bar                  Nightclub  60.169658   
39                         Café Huvila                       Café  60.174610   
40                     Sushibar + Wine           Sushi Restaurant  60.167187   
41                Yrjönkadun uimahalli                       Pool  60.168234   
42  Hakasalmen huvila / Villa Hagasund                Art Gallery  60.174406   
43                       Fantasiapelit                 Hobby Shop  60.169461   
44           Patisserie Teemu & Markus                     Bakery  60.167899   
45                              Passio    Scandinavian Restaurant  60.167088   
46                                Vans                 Shoe Store  60.169564   
47                          Q-teatteri              Indie Theater  60.174097   
48                         Ruohonjuuri            Organic Grocery  60.169568   
49                              Br

In [22]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


In [23]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=14) # generate map 

for lat, lng, label in zip(nearby_venues.lat, nearby_venues.lng, nearby_venues.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='black',
        popup=label,
        fill = True,
        fill_color='magenta',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Search for Hotels

In [24]:
# search for hotels
search_query = 'Hotel'
radius = 500

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Hotel&radius=500&limit=100'

In [25]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedecaf1e152c001bd3b3a1'},
 'response': {'venues': [{'id': '4adcdb1ef964a520565f21e3',
    'name': 'Hotel Kämp',
    'location': {'address': 'Pohjoisesplanadi 29',
     'lat': 60.16812016130064,
     'lng': 24.94711484328597,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.16812016130064,
       'lng': 24.94711484328597}],
     'distance': 263,
     'postalCode': '00100',
     'cc': 'FI',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Pohjoisesplanadi 29', '00100 Helsinki', 'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d1fa931735',
      'name': 'Hotel',
      'pluralName': 'Hotels',
      'shortName': 'Hotel',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/hotel_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592651040',
    'hasPerk': False},
   {'id': '4adcdb1ef964a520645f21e3',
    'name': 'Rivoli Hotel Jardin',
    'l

In [26]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                 name  \
0  4adcdb1ef964a520565f21e3           Hotel Kämp   
1  4adcdb1ef964a520645f21e3  Rivoli Hotel Jardin   
2  4adcdb1ff964a520845f21e3     GLO Hotel Kluuvi   
3  4f87c924e4b09582a0cb49a3            Hotel Gym   
4  4adcdb1ef964a5204a5f21e3        Klaus K Hotel   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d1fa931735', 'name': 'H...  v-1592651040    False   
1  [{'id': '4bf58dd8d48988d1fa931735', 'name': 'H...  v-1592651040    False   
2  [{'id': '4bf58dd8d48988d1fa931735', 'name': 'H...  v-1592651040    False   
3  [{'id': '4bf58dd8d48988d176941735', 'name': 'G...  v-1592651040    False   
4  [{'id': '4bf58dd8d48988d1fa931735', 'name': 'H...  v-1592651040    False   

      location.address  location.lat  location.lng  \
0  Pohjoisesplanadi 29     60.168120     24.947115   
1       Kasarmikatu 40     60.165646     24.947117   
2         Kluuvikatu 4     60.168675     24.947322   
3        Klaus K Hotel     60.166328     24.942852   
4        Bulevardi 2-4     60.166194     24.942263   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.16812016130064...                263   
1  [{'label': 'display', 'lat': 60.16564602594707...                319   
2  [{'label': 'display', 'lat': 60.16867529539493...                298   
3  [{'label': 'display', 'lat': 60.16632793554025...                121   
4  [{'label': 'display', 'lat': 60.16619364854354...                136   

  location.postalCode location.cc location.city location.state  \
0               00100          FI      Helsinki        Uusimaa   
1               00130          FI      Helsinki        Uusimaa   
2               00100          FI      Helsinki        Uusimaa   
3               00120          FI      Helsinki        Uusimaa   
4               00120          FI      Helsinki            NaN   

  location.country                          location.formattedAddress  \
0            Suomi       [Pohjoisesplanadi 29, 00100 Helsinki, Suomi]   
1            Suomi            [Kasarmikatu 40, 00130 Helsinki, Suomi]   
2            Suomi              [Kluuvikatu 4, 00100 Helsinki, Suomi]   
3            Suomi  [Klaus K Hotel (Bulevardi 2-4), 00120 Helsinki...   
4            Suomi             [Bulevardi 2-4, 00120 Helsinki, Suomi]   

  location.crossStreet location.neighborhood venuePage.id  
0                  NaN                   NaN          NaN  
1                  NaN                   NaN          NaN  
2                  NaN                   NaN          NaN  
3        Bulevardi 2-4                   NaN          NaN  
4                  NaN                   NaN          NaN

In [27]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered

name            categories  \
0                                          Hotel Kämp                 Hotel   
1                                 Rivoli Hotel Jardin                 Hotel   
2                                    GLO Hotel Kluuvi                 Hotel   
3                                           Hotel Gym                   Gym   
4                                       Klaus K Hotel                 Hotel   
5                                 Hotel GLO Spa & Gym  Gym / Fitness Center   
6                     Solo Sokos Hotel Torni Helsinki                 Hotel   
7                       Original Sokos Hotel Helsinki                 Hotel   
8                            Radisson Blu Plaza Hotel                 Hotel   
9   Original Sokos Hotel Helsinki Staff Refreshmen...                Office   
10                  Hotel Indigo Helsinki - Boulevard                 Hotel   
11                       Original Sokos Hotel Vaakuna                 Hotel   
12                        Original Sokos Hotel Albert                 Hotel   
13                        Hotel Marski neukkari Filip                  None   
14                                       Hotelli Finn                 Hotel   
15                                   Hotel St. George                 Hotel   
16                            Hotel Kämp Upper Lounge                Lounge   
17                              Hotel Kämp Banquettes     Convention Center   
18                                      Omena Hotelli                 Hotel   
19                             hotel kamp health club  Gym / Fitness Center   
20                  Scandic Hotel Marski terassisauna                  None   
21                             hotel vaakuna vip room                Hostel   
22                                           Hotel F6                 Hotel   
23                            Hotel Manta of Helsinki     Outdoor Sculpture   
24                    solo sokos hotel torni aamupala        Breakfast Spot   
25                                         Hotel Anna                 Hotel   
26                                        Hötel haven                 Hotel   
27                                        Hotel Haven                 Hotel   
28                                       Hotel Arhtur                 Hotel   
29                                      Omena Hotelli                 Hotel   
30                       Sauna @ Sokos Hotel Helsinki    Sauna / Steam Room   
31                              sokos hotel penthouse                Lounge   
32                     Sokos Hotel Helsingin Aamupala        Breakfast Spot   
33                       Sauna in Sokos Hotel Vaakuna    Sauna / Steam Room   
34                                 Rodbergs hotel&bar                Lounge   
35                         Best Western Hotel Carlton                 Hotel   
36                          Taxitolppa Marski Hotelli            Taxi Stand   
37                                 GYM radisson hotel                   Gym   
38               Urbano-kabinetti, Sokos Hotel Albert          Meeting Room   
39                                          Sky Lofts                 Hotel   
40                                         LIVINGROOM        Breakfast Spot   
41                                Scandic Simonkenttä                 Hotel   
42                                          Hotelfinn              Building   
43                       Hotelli Tornin taksiasema 27            Taxi Stand   
44                                    Ravintola Torni            Restaurant   
45                              Henkilökunnan ruokala             Cafeteria   
46                        Hotelli Kämpin taksiasema 4            Taxi Stand   
47                                Hotell Milton Plaza                 Hotel   
48                                   Antica-kabinetti           Event Space   
49                                  Scandic Hotels HQ                Office   

                   

In [28]:
dataframe_filtered.name

0                                            Hotel Kämp
1                                   Rivoli Hotel Jardin
2                                      GLO Hotel Kluuvi
3                                             Hotel Gym
4                                         Klaus K Hotel
5                                   Hotel GLO Spa & Gym
6                       Solo Sokos Hotel Torni Helsinki
7                         Original Sokos Hotel Helsinki
8                              Radisson Blu Plaza Hotel
9     Original Sokos Hotel Helsinki Staff Refreshmen...
10                    Hotel Indigo Helsinki - Boulevard
11                         Original Sokos Hotel Vaakuna
12                          Original Sokos Hotel Albert
13                          Hotel Marski neukkari Filip
14                                         Hotelli Finn
15                                     Hotel St. George
16                              Hotel Kämp Upper Lounge
17                                Hotel Kämp Ban

In [29]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=15) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='black',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Search for Restaurants

In [30]:
# search for restaurants
search_query = 'Restaurant'
radius = 500

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Restaurant&radius=500&limit=100'

In [31]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eededf377af03001bdf472c'},
 'response': {'venues': [{'id': '51737bdfe4b0cb9cbb55b445',
    'name': 'The Restaurant',
    'location': {'address': 'Scandic Simonkenttä',
     'crossStreet': 'Simonkatu 9',
     'lat': 60.169019354459884,
     'lng': 24.93528181493337,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.169019354459884,
       'lng': 24.93528181493337}],
     'distance': 441,
     'postalCode': '00100',
     'cc': 'FI',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Scandic Simonkenttä (Simonkatu 9)',
      '00100 Helsinki',
      'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d143941735',
      'name': 'Breakfast Spot',
      'pluralName': 'Breakfast Spots',
      'shortName': 'Breakfast',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/breakfast_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592651193',
    'hasPer

In [32]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                             name  \
0  51737bdfe4b0cb9cbb55b445                   The Restaurant   
1  4c6e9b2d4d24b60c9c17d9d8              Huacheng Restaurant   
2  4dd6b051b0fb8af3807378fb            Restaurant Kämp Signé   
3  521080ed498e03cdccce7279  Restaurant day | Laivurin letut   
4  4d08d4140ead8cfae8f0f176                 Restaurant Pidot   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d143941735', 'name': 'B...  v-1592651193    False   
1  [{'id': '4bf58dd8d48988d145941735', 'name': 'C...  v-1592651193    False   
2  [{'id': '4bf58dd8d48988d1c4941735', 'name': 'R...  v-1592651193    False   
3  [{'id': '4bf58dd8d48988d1c7941735', 'name': 'S...  v-1592651193    False   
4  [{'id': '4bf58dd8d48988d147941735', 'name': 'D...  v-1592651193    False   

       location.address location.crossStreet  location.lat  location.lng  \
0   Scandic Simonkenttä          Simonkatu 9     60.169019     24.935282   
1                 Forum                  NaN     60.169352     24.938121   
2   Pohjoisesplanadi 29                  NaN     60.167638     24.947141   
3  Sinebrykoffin puisto                  NaN     60.167567     24.932599   
4                   NaN                  NaN     60.166787     24.951863   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.16901935445988...                441   
1  [{'label': 'display', 'lat': 60.169352070297, ...                328   
2  [{'label': 'display', 'lat': 60.16763846981376...                254   
3  [{'label': 'display', 'lat': 60.16756692843562...                552   
4  [{'label': 'display', 'lat': 60.166787, 'lng':...                518   

  location.postalCode location.cc location.city location.state  \
0               00100          FI      Helsinki        Uusimaa   
1               00100          FI      Helsinki        Uusimaa   
2               00100          FI      Helsinki        Uusimaa   
3                 NaN          FI      Helsinki        Uusimaa   
4                 NaN          FI           NaN            NaN   

  location.country                          location.formattedAddress  \
0            Suomi  [Scandic Simonkenttä (Simonkatu 9), 00100 Hels...   
1            Suomi                     [Forum, 00100 Helsinki, Suomi]   
2            Suomi       [Pohjoisesplanadi 29, 00100 Helsinki, Suomi]   
3            Suomi            [Sinebrykoffin puisto, Helsinki, Suomi]   
4            Suomi                                            [Suomi]   

  venuePage.id location.neighborhood  
0          NaN                   NaN  
1          NaN                   NaN  
2          NaN                   NaN  
3          NaN                   NaN  
4          NaN                   NaN

In [33]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered

name                  categories  \
0                     The Restaurant              Breakfast Spot   
1                Huacheng Restaurant          Chinese Restaurant   
2              Restaurant Kämp Signé                  Restaurant   
3    Restaurant day | Laivurin letut                 Snack Place   
4                   Restaurant Pidot                       Diner   
5                   Restaurant Haven              Breakfast Spot   
6              Center-inn Restaurant             Other Nightlife   
7   Michel Restaurant & Cocktail Bar  Modern European Restaurant   
8                  Nanglo Restaurant           Indian Restaurant   
9               Sokos Restaurant&Bar                Burger Joint   
10            Point Restaurant & Bar                      Buffet   
11                Holiday Restaurant                  Restaurant   
12                Pasha's Restaurant        Fast Food Restaurant   
13       Simonkatu Restaurant & Cafe                  Restaurant   
14      Scandinavian Fish Restaurant           Fish & Chips Shop   
15                    #Restaurantday                  Restaurant   
16                  Plaza Restaurant              Breakfast Spot   
17                   Café Strindberg                        Café   
18                           Kappeli                        Café   
19                             Penny         American Restaurant   
20                  Café Lasipalatsi                 Coffee Shop   
21                           Mei Lin         Szechuan Restaurant   
22                    Virgin Oil Co.          Italian Restaurant   
23                    Ravintola Aino     Scandinavian Restaurant   
24                    BW Restaurants                      Office   
25                           Nanking          Chinese Restaurant   
26                   Ravintola Savoy     Scandinavian Restaurant   
27                 Dennis Napoletana                 Pizza Place   
28                              TPAS            Tapas Restaurant   
29                            Loiste     Scandinavian Restaurant   
30                   Ravintola Monal     North Indian Restaurant   
31                 Ravintola Kitzens                  Restaurant   
32                    Un Cerdo Ciego                 Pop-Up Shop   
33                       Pääkonttori     Scandinavian Restaurant   
34         Happy Hour Restaurants Oy                      Office   

                            address        crossStreet        lat        lng  \
0               Scandic Simonkenttä        Simonkatu 9  60.169019  24.935282   
1                             Forum                NaN  60.169352  24.938121   
2               Pohjoisesplanadi 29                NaN  60.167638  24.947141   
3              Sinebrykoffin puisto                NaN  60.167567  24.932599   
4                               NaN                NaN  60.166787  24.951863   
5                               NaN                NaN  60.166550  24.951908   
6                               NaN                NaN  60.168473  24.945148   
7                       Mikonkatu 4                NaN  60.168582  24.945508   
8                               NaN                NaN  60.166780  24.936005   
9                               NaN                NaN  60.169781  24.947398   
10             Iso Roobertinkatu 10                NaN  60.163773  24.942982   
11                              NaN                NaN  60.165028  24.935455   
12                   Eerikinkatu 14                NaN  60.166900  24.934793   
13                              NaN                NaN  60.168956  24.935208   
14                       Kauppatori                NaN  60.167492  24.952763   
15                              NaN                NaN  60.169599  24.939993   
16                     Mikonkatu 23                NaN  60.172293  24.945540   
17              Pohjoisesplanadi 33                NaN  60.167690  24.946243   
18                 Eteläesplanadi 1                NaN  60.1673

In [34]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=15) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='black',
        popup=label,
        fill = True,
        fill_color='green',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Search for Gift Shop

In [46]:
# search for gift shop
search_query = 'Gift Shop'
radius = 1000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url


'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Gift Shop&radius=1000&limit=100'

In [47]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf0b30de0d9001bee6925'},
 'response': {'venues': [{'id': '564c6236498e50af0cdc0a83',
    'name': 'Gift Shop Nordis',
    'location': {'address': 'Arkadiankatu 4-6',
     'lat': 60.17121,
     'lng': 24.935084,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.17121,
       'lng': 24.935084}],
     'distance': 592,
     'cc': 'FI',
     'neighborhood': 'Kamppi',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Arkadiankatu 4-6', 'Helsinki', 'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d128951735',
      'name': 'Gift Shop',
      'pluralName': 'Gift Shops',
      'shortName': 'Gift Shop',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/shops/giftshop_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592651982',
    'hasPerk': False},
   {'id': '5177ffcf498ee83487dc47bd',
    'name': 'Solo Shop',
    'location': {'address': 'Mannerheim

In [48]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id              name  \
0  564c6236498e50af0cdc0a83  Gift Shop Nordis   
1  5177ffcf498ee83487dc47bd         Solo Shop   
2  4d8a0aadd85f37046c91f4db        Apple Shop   
3  54e2fabc498e7eda5e2c60a4        Apple Shop   
4  4c5419c6a724e21e9797d2f5       Moomin Shop   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d128951735', 'name': 'G...  v-1592651982    False   
1  [{'id': '4bf58dd8d48988d106951735', 'name': 'M...  v-1592651982    False   
2  [{'id': '4bf58dd8d48988d122951735', 'name': 'E...  v-1592651982    False   
3  [{'id': '4bf58dd8d48988d122951735', 'name': 'E...  v-1592651982    False   
4  [{'id': '4bf58dd8d48988d128951735', 'name': 'G...  v-1592651982    False   

      location.address  location.lat  location.lng  \
0     Arkadiankatu 4-6     60.171210     24.935084   
1    Mannerheimintie 6     60.167305     24.942498   
2  Aleksanterinkatu 52     60.168598     24.941870   
3             Gigantti     60.169414     24.937967   
4   Mannerheimintie 20     60.169265     24.938044   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.17121, 'lng': ...                592   
1  [{'label': 'display', 'lat': 60.16730520549474...                 12   
2  [{'label': 'display', 'lat': 60.16859801261521...                137   
3  [{'label': 'display', 'lat': 60.16941430729947...                339   
4  [{'label': 'display', 'lat': 60.16926451665104...                324   

  location.cc location.neighborhood location.city    location.state  \
0          FI                Kamppi      Helsinki           Uusimaa   
1          FI                   NaN      Helsinki           Uusimaa   
2          FI                   NaN      Helsinki           Uusimaa   
3          FI                   NaN      Helsinki           Uusimaa   
4          FI                   NaN      Helsinki  Southern Finland   

  location.country                          location.formattedAddress  \
0            Suomi                [Arkadiankatu 4-6, Helsinki, Suomi]   
1            Suomi         [Mannerheimintie 6, 00100 Helsinki, Suomi]   
2            Suomi  [Aleksanterinkatu 52 (7. krs), 00100 Helsinki,...   
3            Suomi  [Gigantti (Kauppakeskus Forum, Mannerheimintie...   
4            Suomi  [Mannerheimintie 20 (Mannerheimintie 20), 0010...   

  location.postalCode                      location.crossStreet venuePage.id  
0                 NaN                                       NaN          NaN  
1               00100                                       NaN          NaN  
2               00100                                    7. krs          NaN  
3               00100  Kauppakeskus Forum, Mannerheimintie 20 B          NaN  
4               00100                        Mannerheimintie 20          NaN

In [49]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered

dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Gift Shop'] 
dataframe_filtered

name categories                address  \
0                 Gift Shop Nordis  Gift Shop       Arkadiankatu 4-6   
4                      Moomin Shop  Gift Shop     Mannerheimintie 20   
8                      Moomin Shop  Gift Shop           Keskuskatu 1   
18  Lahja Rosa Gift And Decorstion  Gift Shop                    NaN   
28                 The Candle Shop  Gift Shop                    NaN   
40                     Moomin Shop  Gift Shop  Mannerheimintie 22-24   
47                   Amos Rex Shop  Gift Shop               Amos Rex   

          lat        lng                                     labeledLatLngs  \
0   60.171210  24.935084  [{'label': 'display', 'lat': 60.17121, 'lng': ...   
4   60.169265  24.938044  [{'label': 'display', 'lat': 60.16926451665104...   
8   60.168210  24.943611  [{'label': 'display', 'lat': 60.16821, 'lng': ...   
18  60.165217  24.936299  [{'label': 'display', 'lat': 60.165217, 'lng':...   
28  60.168777  24.938100  [{'label': 'display', 'lat': 60.168777, 'lng':...   
40  60.169830  24.937001  [{'label': 'display', 'lat': 60.16983, 'lng': ...   
47  60.170534  24.936657  [{'label': 'display', 'lat': 60.170534, 'lng':...   

    distance  cc neighborhood      city             state country  \
0        592  FI       Kamppi  Helsinki           Uusimaa   Suomi   
4        324  FI          NaN  Helsinki  Southern Finland   Suomi   
8        105  FI          NaN  Helsinki           Uusimaa   Suomi   
18       424  FI          NaN       NaN               NaN   Suomi   
28       290  FI          NaN  Helsinki           Uusimaa   Suomi   
40       409  FI          NaN  Helsinki           Uusimaa   Suomi   
47       477  FI          NaN  Helsinki           Uusimaa   Suomi   

                                     formattedAddress postalCode  \
0                 [Arkadiankatu 4-6, Helsinki, Suomi]        NaN   
4   [Mannerheimintie 20 (Mannerheimintie 20), 0010...      00100   
8               [Keskuskatu 1, 00100 Helsinki, Suomi]      00100   
18                                            [Suomi]        NaN   
28                            [00100 Helsinki, Suomi]      00100   
40     [Mannerheimintie 22-24, 00100 Helsinki, Suomi]      00100   
47  [Amos Rex (Mannerheimintie 22-24), 00100 Helsi...      00100   

              crossStreet                        id  
0                     NaN  564c6236498e50af0cdc0a83  
4      Mannerheimintie 20  4c5419c6a724e21e9797d2f5  
8                     NaN  5e4d209db061700007ba538d  
18                    NaN  5131f59de4b09cc35eb20df2  
28                    NaN  5c659e77e55d8b002def5e40  
40                    NaN  5e36d27bc0236b000874b0cc  
47  Mannerheimintie 22-24  5da44189b72abe0008d25002

In [50]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=15) # generate map

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='maroon',
        popup=label,
        fill = True,
        fill_color='red',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Search for Museum

In [40]:
# search for Museum
search_query = 'Museum'
radius = 1200

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Museum&radius=1200&limit=100'

In [41]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf038618f43001b9d2d8e'},
 'response': {'venues': [{'id': '4be54dec2468c928c1dbff42',
    'name': 'Sinebrychoffin Taidemuseo / Sinebrychoff Art Museum',
    'location': {'address': 'Bulevardi 40',
     'lat': 60.16252598185265,
     'lng': 24.932166499264948,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.16252598185265,
       'lng': 24.932166499264948}],
     'distance': 792,
     'postalCode': '00120',
     'cc': 'FI',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Bulevardi 40', '00120 Helsinki', 'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d18f941735',
      'name': 'Art Museum',
      'pluralName': 'Art Museums',
      'shortName': 'Art Museum',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/museum_art_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592651803',
    'hasPerk': False},
   {'id': '4adcdb2

In [42]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id  \
0  4be54dec2468c928c1dbff42   
1  4adcdb23f964a520b46021e3   
2  4adcdb23f964a520d16021e3   
3  4ca5a9b276d3a09368c7f96a   
4  5739cd43498e153306bc8d36   

                                                name  \
0  Sinebrychoffin Taidemuseo / Sinebrychoff Art M...   
1  Suomen arkkitehtuurimuseo (Museum of Finnish A...   
2  Helsingin kaupunginmuseo / Helsinki City Museu...   
3                        Sotamuseo | Military museum   
4                     Museum of broken relationships   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d18f941735', 'name': 'A...  v-1592651803    False   
1  [{'id': '4bf58dd8d48988d18f941735', 'name': 'A...  v-1592651803    False   
2  [{'id': '4bf58dd8d48988d190941735', 'name': 'H...  v-1592651803    False   
3  [{'id': '4bf58dd8d48988d190941735', 'name': 'H...  v-1592651803    False   
4  [{'id': '4bf58dd8d48988d18f941735', 'name': 'A...  v-1592651803    False   

      location.address  location.lat  location.lng  \
0         Bulevardi 40     60.162526     24.932166   
1       Kasarmikatu 24     60.163133     24.947763   
2     Sederholmin talo     60.168996     24.954028   
3         Liisankatu 1     60.174661     24.960552   
4  Aleksanterinkatu 16     60.168919     24.953990   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.16252598185265...                792   
1  [{'label': 'display', 'lat': 60.16313278071235...                556   
2  [{'label': 'display', 'lat': 60.168996, 'lng':...                658   
3  [{'label': 'display', 'lat': 60.17466110631173...               1281   
4  [{'label': 'display', 'lat': 60.16891865697694...                653   

  location.postalCode location.cc location.city location.state  \
0               00120          FI      Helsinki        Uusimaa   
1               00130          FI      Helsinki        Uusimaa   
2               00170          FI      Helsinki        Uusimaa   
3               00170          FI      Helsinki        Uusimaa   
4                 NaN          FI      Helsinki        Uusimaa   

  location.country                          location.formattedAddress  \
0            Suomi              [Bulevardi 40, 00120 Helsinki, Suomi]   
1            Suomi            [Kasarmikatu 24, 00130 Helsinki, Suomi]   
2            Suomi  [Sederholmin talo (Aleksanterinkatu 16–18), 00...   
3            Suomi              [Liisankatu 1, 00170 Helsinki, Suomi]   
4            Suomi             [Aleksanterinkatu 16, Helsinki, Suomi]   

     location.crossStreet venuePage.id location.neighborhood  
0                     NaN          NaN                   NaN  
1                     NaN          NaN                   NaN  
2  Aleksanterinkatu 16–18          NaN                   NaN  
3                     NaN          NaN                   NaN  
4                     NaN          NaN                   NaN

In [43]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered

name      categories  \
0   Sinebrychoffin Taidemuseo / Sinebrychoff Art M...      Art Museum   
1   Suomen arkkitehtuurimuseo (Museum of Finnish A...      Art Museum   
2   Helsingin kaupunginmuseo / Helsinki City Museu...  History Museum   
3                         Sotamuseo | Military museum  History Museum   
4                      Museum of broken relationships      Art Museum   
5                           Design Museum Sun Terrace            None   
6                                 helsinki art museum      Art Museum   
7                                   Teddy Bear Museum          Museum   
8                                             Ateneum      Art Museum   
9                                              Kiasma      Art Museum   
10                                        Designmuseo      Art Museum   
11                         Amos Andersonin taidemuseo      Art Museum   
12                                                HAM      Art Museum   
13                              Suomen Kansallismuseo  History Museum   
14                 Hakasalmen huvila / Villa Hagasund     Art Gallery   
15                            Suomen Pankin Rahamuseo          Museum   
16                          Luonnontieteellinen museo  Science Museum   
17                           Helsingin yliopistomuseo  History Museum   

                      address        lat        lng  \
0                Bulevardi 40  60.162526  24.932166   
1              Kasarmikatu 24  60.163133  24.947763   
2            Sederholmin talo  60.168996  24.954028   
3                Liisankatu 1  60.174661  24.960552   
4         Aleksanterinkatu 16  60.168919  24.953990   
5            Korkeavuorenkatu  60.169371  24.935975   
6                         NaN  60.169342  24.931468   
7                         NaN  60.167995  24.967583   
8                 Kaivokatu 2  60.170302  24.943788   
9         Mannerheiminaukio 2  60.171652  24.936537   
10        Korkeavuorenkatu 23  60.163145  24.946401   
11               Yrjönkatu 27  60.168389  24.937459   
12   Eteläinen Rautatiekatu 8  60.169792  24.930432   
13         Mannerheimintie 34  60.174927  24.931978   
14        Mannerheimintie 13b  60.174406  24.933136   
15           Snellmaninkatu 2  60.170180  24.953100   
16  Pohjoinen Rautatiekatu 13  60.171350  24.931549   
17           Yliopistonkatu 3  60.170220  24.948430   

                                       labeledLatLngs  distance postalCode  \
0   [{'label': 'display', 'lat': 60.16252598185265...       792      00120   
1   [{'label': 'display', 'lat': 60.16313278071235...       556      00130   
2   [{'label': 'display', 'lat': 60.168996, 'lng':...       658      00170   
3   [{'label': 'display', 'lat': 60.17466110631173...      1281      00170   
4   [{'label': 'display', 'lat': 60.16891865697694...       653        NaN   
5   [{'label': 'display', 'lat': 60.16937098888402...       425        NaN   
6   [{'label': 'display', 'lat': 60.169342, 'lng':...       651        NaN   
7   [{'label': 'display', 'lat': 60.167995, 'lng':...      1386        NaN   
8   [{'label': 'display', 'lat': 60.17030164536989...       328      00100   
9   [{'label': 'display', 'lat': 60.17165167467719...       578      00100   
10  [{'label': 'display', 'lat': 60.16314485405816...       519      00130   
11  [{'label': 'display', 'lat': 60.16838895208326...       303      00100   
12  [{'label': 'display', 'lat': 60.16979212211695...       722      00100   
13  [{'label': 'display', 'lat': 60.174927, 'lng':...      1022      00100   
14  [{'label': 'display', 'lat': 60.17440631411392...       938      00100   
15  [{'label': 'display', 'lat': 60.17018, 'lng': ...       659      00170   
16  [{'label': 'display', 'lat': 60.171349882576, ...       751      00100   
17  [{'label': 'display', 'lat': 60.17022, 'lng': ...       450      00100   

    cc      city    state country  \
0   FI  Helsinki  Uusimaa   Suomi   
1   FI  Helsinki  Uusimaa   Suomi   
2   FI  Helsinki  Uus

In [45]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=14) # generate map c

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='purple',
        popup=label,
        fill = True,
        fill_color='',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Search for Cafe

In [35]:
# search for cafe
search_query = 'Café'
radius = 1000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Café&radius=1000&limit=100'

In [36]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedeea214a126001b26b0a0'},
 'response': {'venues': [{'id': '4adcdb1ff964a5208d5f21e3',
    'name': 'Fazer Café',
    'location': {'address': 'Kluuvikatu 3',
     'lat': 60.16864,
     'lng': 24.947746,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.16864,
       'lng': 24.947746}],
     'distance': 317,
     'postalCode': '00100',
     'cc': 'FI',
     'neighborhood': 'Kluuvi, Helsinki',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Kluuvikatu 3', '00100 Helsinki', 'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d16d941735',
      'name': 'Café',
      'pluralName': 'Cafés',
      'shortName': 'Café',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/cafe_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592651528',
    'hasPerk': False},
   {'id': '4f7d607fe4b0ffb6a37cdd8a',
    'name': 'Hard Rock Cafe Helsinki',
    'location':

In [37]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                     name  \
0  4adcdb1ff964a5208d5f21e3               Fazer Café   
1  4f7d607fe4b0ffb6a37cdd8a  Hard Rock Cafe Helsinki   
2  4c4aced0959220a1a7c3a40e                   Café 4   
3  4cf0c872e9425481fc6466c5           Mövenpick cafe   
4  4adcdb1ff964a5208b5f21e3  Konditoria Café Briossi   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d16d941735', 'name': 'C...  v-1592651528    False   
1  [{'id': '56aa371be4b08b9a8d573538', 'name': 'T...  v-1592651528    False   
2  [{'id': '4bf58dd8d48988d16d941735', 'name': 'C...  v-1592651528    False   
3  [{'id': '4bf58dd8d48988d16d941735', 'name': 'C...  v-1592651528    False   
4  [{'id': '4bf58dd8d48988d16a941735', 'name': 'B...  v-1592651528    False   

      location.address  location.lat  location.lng  \
0         Kluuvikatu 3     60.168640     24.947746   
1  Aleksanterinkatu 21     60.168896     24.941295   
2   Aleksanterikatu 52     60.168165     24.941120   
3  Aleksanterinkatu 52     60.168127     24.941405   
4        Kalevankatu 9     60.167562     24.938312   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.16864, 'lng': ...                317   
1  [{'label': 'display', 'lat': 60.1688957, 'lng'...                180   
2  [{'label': 'display', 'lat': 60.16816497742627...                116   
3  [{'label': 'display', 'lat': 60.168127, 'lng':...                102   
4  [{'label': 'display', 'lat': 60.167562, 'lng':...                236   

  location.postalCode location.cc location.neighborhood location.city  \
0               00100          FI      Kluuvi, Helsinki      Helsinki   
1               00100          FI                   NaN      Helsinki   
2               00100          FI                   NaN      Helsinki   
3               00100          FI                   NaN      Helsinki   
4               00100          FI                   NaN      Helsinki   

       location.state location.country  \
0             Uusimaa            Suomi   
1  Etelä-Suomen Lääni            Suomi   
2             Uusimaa            Suomi   
3             Uusimaa            Suomi   
4             Uusimaa            Suomi   

                           location.formattedAddress venuePage.id  \
0              [Kluuvikatu 3, 00100 Helsinki, Suomi]          NaN   
1       [Aleksanterinkatu 21, 00100 Helsinki, Suomi]     87576934   
2  [Aleksanterikatu 52 (4. krs), 00100 Helsinki, ...          NaN   
3       [Aleksanterinkatu 52, 00100 Helsinki, Suomi]          NaN   
4             [Kalevankatu 9, 00100 Helsinki, Suomi]          NaN   

  location.crossStreet  
0                  NaN  
1                  NaN  
2               4. krs  
3                  NaN  
4                  NaN

In [38]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Café'] 
dataframe_filtered

name categories              address        lat  \
0                     Fazer Café       Café         Kluuvikatu 3  60.168640   
2                         Café 4       Café   Aleksanterikatu 52  60.168165   
3                 Mövenpick cafe       Café  Aleksanterinkatu 52  60.168127   
6                    Kiasma Café       Café  Mannerheiminaukio 2  60.171662   
8                     Cafe Posto       Café      Lönnrotinkatu 9  60.166090   
9                     Fazer Café       Café           Citycenter  60.169784   
10           Cafe Kluuvi by Illy       Café  Kauppakeskus Kluuvi  60.169467   
12                  Cafe & Choco       Café                  NaN  60.168003   
13              Fazer Café Forum       Café                Forum  60.169344   
14                  Cafe Pequeño       Café         Kasarmintori  60.165528   
17                   Café Artist       Café      Svenska Teatern  60.167347   
21                Cafe Arppeanum       Café     Snellmaninkatu 3  60.169763   
22              Scandinavia Cafe       Café    Vanha Kauppahalli  60.166064   
23  Cafe Kiosk Kaisaniemenpuisto       Café                  NaN  60.173923   
24                 Café Esplanad       Café  Pohjoisesplanadi 37  60.167750   
26                    Café Aalto       Café  Pohjoisesplanadi 39  60.167825   
27                   Cafe Thalia       Café                  NaN  60.167067   
28                    Café Amico       Café                  NaN  60.169771   
30           cafe Antell Arkadia       Café      Arkadiankatu 23  60.171386   
31                     Mori Cafe       Café    Mannerheimintie 8  60.167220   
32                    Café Maria       Café   Lapinlahdenkatu 16  60.166903   
34               Café Strindberg       Café  Pohjoisesplanadi 33  60.167690   
37                  Cafe Zoceria       Café  Aleksanterinkatu 15  60.168945   
39                    cafe soffa       Café   Mannerheimintie 14  60.168558   
40                   Cafe-Kioski       Café                  NaN  60.167305   
42             Bike Café Finland       Café                  NaN  60.167354   
44                          Cafe       Café  Uudenmaankatu 19-21  60.163845   
45                    Café Engel       Café  Aleksanterinkatu 26  60.169306   
46                      Cafe LOV       Café      Mariankatu 13 B  60.171284   
47                     Café Amos       Café         Yrjönkatu 27  60.168405   
48                     Café Yrjö       Café         Yrjönkatu 21  60.168421   
49              Green Hippo Café       Café     Punavuorenkatu 2  60.161875   

          lng                                     labeledLatLngs  distance  \
0   24.947746  [{'label': 'display', 'lat': 60.16864, 'lng': ...       317   
2   24.941120  [{'label': 'display', 'lat': 60.16816497742627...       116   
3   24.941405  [{'label': 'display', 'lat': 60.168127, 'lng':...       102   
6   24.936504  [{'label': 'display', 'lat': 60.17166198557313...       580   
8   24.937657  [{'label': 'display', 'lat': 60.16609, 'lng': ...       309   
9   24.941829  [{'label': 'display', 'lat': 60.16978358327019...       267   
10  24.947810  [{'label': 'display', 'lat': 60.16946702024972...       369   
12  24.943032  [{'label': 'display', 'lat': 60.168003, 'lng':...        70   
13  24.938012  [{'label': 'display', 'lat': 60.16934355803721...       332   
14  24.949162  [{'label': 'display', 'lat': 60.165528, 'lng':...       420   
17  24.943071  [{'label': 'display', 'lat': 60.167347, 'lng':...        28   
21  24.953437  [{'label': 'display', 'lat': 60.16976309799274...       655   
22  24.952992  [{'label': 'display', 'lat': 60.16606448020363...       595   
23  24.944323  [{'label': 'display', 'lat': 60.17392258514022...       731   
24  24.944577  [{'label': 'display', 'lat': 60.16775002876532...       117   
26  24.943540  [{'label': 'display', 'lat': 60.16782505897748...        70   
27  24.942275  [{'label': 'display', 'lat': 60.16706730635121...        41   
28  24.926629  [

In [39]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=15) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='maroon',
        popup=label,
        fill = True,
        fill_color='',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

# Search for Emergency Services

## Search for Hospitals

In [94]:
# search for hospitals
search_query = 'Hospital'
radius = 4000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Hospital&radius=4000&limit=100'

In [95]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf57583525f001b21e587'},
 'response': {'venues': [{'id': '54929c8c498efdb6a0fc6e63',
    'name': 'Helsinki Hospital',
    'location': {'address': 'Bulevardi 22',
     'lat': 60.16436767578125,
     'lng': 24.937091827392578,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.16436767578125,
       'lng': 24.937091827392578}],
     'distance': 454,
     'cc': 'FI',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Bulevardi 22', 'Helsinki', 'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d196941735',
      'name': 'Hospital',
      'pluralName': 'Hospitals',
      'shortName': 'Hospital',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/medical_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592653263',
    'hasPerk': False},
   {'id': '52ce8fb7498e78ed2bbcecac',
    'name': 'Coxa, Hospital for joint replacement',
    'location':

In [96]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id  \
0  54929c8c498efdb6a0fc6e63   
1  52ce8fb7498e78ed2bbcecac   
2  4eeb6060490111d46a61c723   
3  5d79f5a502368900072aebd8   
4  4ce25a8169136dcb02b2eee6   

                                                name  \
0                                  Helsinki Hospital   
1               Coxa, Hospital for joint replacement   
2                               St. Lesters Hospital   
3  Kahvio/Cafeteria, Uusi Lastensairaala/New Chil...   
4                                    Töölön sairaala   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d196941735', 'name': 'H...  v-1592653263    False   
1  [{'id': '4bf58dd8d48988d177941735', 'name': 'D...  v-1592653263    False   
2  [{'id': '4bf58dd8d48988d1b3941735', 'name': 'M...  v-1592653263    False   
3  [{'id': '4bf58dd8d48988d128941735', 'name': 'C...  v-1592653263    False   
4  [{'id': '4bf58dd8d48988d196941735', 'name': 'H...  v-1592653263    False   

      location.address  location.lat  location.lng  \
0         Bulevardi 22     60.164368     24.937092   
1  Saukonpaadenranta 2     60.159772     24.909388   
2                  NaN     60.161693     24.894150   
3                  NaN     60.187584     24.910526   
4    Topeliuksenkatu 5     60.181193     24.922204   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.16436767578125...                454   
1  [{'label': 'display', 'lat': 60.159772, 'lng':...               2025   
2  [{'label': 'display', 'lat': 60.16169274907339...               2756   
3  [{'label': 'display', 'lat': 60.187584, 'lng':...               2862   
4  [{'label': 'display', 'lat': 60.18119272255448...               1904   

  location.cc location.city location.state location.country  \
0          FI      Helsinki        Uusimaa            Suomi   
1          FI      Helsinki        Uusimaa            Suomi   
2          FI           NaN            NaN            Suomi   
3          FI      Helsinki        Uusimaa            Suomi   
4          FI      Helsinki        Uusimaa            Suomi   

                    location.formattedAddress location.postalCode  \
0             [Bulevardi 22, Helsinki, Suomi]                 NaN   
1      [Saukonpaadenranta 2, Helsinki, Suomi]                 NaN   
2                                     [Suomi]                 NaN   
3                     [00290 Helsinki, Suomi]               00290   
4  [Topeliuksenkatu 5, 00250 Helsinki, Suomi]               00250   

  location.neighborhood location.crossStreet  
0                   NaN                  NaN  
1                   NaN                  NaN  
2                   NaN                  NaN  
3              Meilahti                  NaN  
4                   NaN                  NaN

In [97]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Hospital'] 
dataframe_filtered

name categories             address        lat        lng  \
0    Helsinki Hospital   Hospital        Bulevardi 22  60.164368  24.937092   
4      Töölön sairaala   Hospital   Topeliuksenkatu 5  60.181193  24.922204   
5  Haartmanin sairaala   Hospital    Haartmaninkatu 4  60.189959  24.908040   
6   Meilahden sairaala   Hospital    Haartmaninkatu 4  60.189333  24.905907   
7     Kivelän sairaala   Hospital  Sibeliuksenkatu 14  60.180682  24.918462   

                                      labeledLatLngs  distance  cc      city  \
0  [{'label': 'display', 'lat': 60.16436767578125...       454  FI  Helsinki   
4  [{'label': 'display', 'lat': 60.18119272255448...      1904  FI  Helsinki   
5  [{'label': 'display', 'lat': 60.18995910705907...      3155  FI  Helsinki   
6  [{'label': 'display', 'lat': 60.18933277202544...      3174  FI  Helsinki   
7  [{'label': 'display', 'lat': 60.18068231435106...      1991  FI  Helsinki   

     state country                              formattedAddress postalCode  \
0  Uusimaa   Suomi               [Bulevardi 22, Helsinki, Suomi]        NaN   
4  Uusimaa   Suomi    [Topeliuksenkatu 5, 00250 Helsinki, Suomi]      00250   
5  Uusimaa   Suomi     [Haartmaninkatu 4, 00290 Helsinki, Suomi]      00290   
6  Uusimaa   Suomi     [Haartmaninkatu 4, 00290 Helsinki, Suomi]      00290   
7  Uusimaa   Suomi  [Sibeliuksenkatu 14, 00250 Eteläinen, Suomi]      00250   

  neighborhood crossStreet                        id  
0          NaN         NaN  54929c8c498efdb6a0fc6e63  
4          NaN         NaN  4ce25a8169136dcb02b2eee6  
5          NaN         NaN  4de61b8eb0fb5cbf0ea832e6  
6          NaN         NaN  4b3ba55bf964a520ec7725e3  
7          NaN         NaN  4bdafbce63c5c9b65cb92568

In [98]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=13) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='maroon',
        popup=label,
        fill = True,
        fill_color='red',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Search for Police Departments

In [99]:
# search for police department
search_query = 'Police'
radius = 5000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Police&radius=5000&limit=100'

In [100]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf65947b43d00230668c9'},
 'response': {'venues': [{'id': '52f86d6a498e4721cd872ff8',
    'name': 'Immigration Police',
    'location': {'lat': 60.19859850203025,
     'lng': 24.92552482387334,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.19859850203025,
       'lng': 24.92552482387334}],
     'distance': 3597,
     'cc': 'FI',
     'country': 'Suomi',
     'formattedAddress': ['Suomi']},
    'categories': [{'id': '4bf58dd8d48988d12e941735',
      'name': 'Police Station',
      'pluralName': 'Police Stations',
      'shortName': 'Police Station',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/government_policestation_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592653368',
    'hasPerk': False}]}}

In [101]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                name  \
0  52f86d6a498e4721cd872ff8  Immigration Police   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d12e941735', 'name': 'P...  v-1592653368    False   

   location.lat  location.lng  \
0     60.198599     24.925525   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.19859850203025...               3597   

  location.cc location.country location.formattedAddress  
0          FI            Suomi                   [Suomi]

In [102]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
dataframe_filtered
# dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Hospital'] 
# dataframe_filtered

name      categories        lat        lng  \
0  Immigration Police  Police Station  60.198599  24.925525   

                                      labeledLatLngs  distance  cc country  \
0  [{'label': 'display', 'lat': 60.19859850203025...      3597  FI   Suomi   

  formattedAddress                        id  
0          [Suomi]  52f86d6a498e4721cd872ff8

In [103]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=12) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='maroon',
        popup=label,
        fill = True,
        fill_color='red',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Tourist Information Centre

In [104]:
# search for Tourist Information
search_query = 'Tourist Information'
radius = 3000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Tourist Information&radius=3000&limit=100'

In [105]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf44fdd0f850023542777'},
 'response': {'venues': [{'id': '5ca2f39aea1e44002c7dccc9',
    'name': 'Helsinki Tourist Information (Helsingin matkailuneuvonta)',
    'location': {'address': 'Kaivokatu 1',
     'lat': 60.170948599705014,
     'lng': 24.941486120224,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.170948599705014,
       'lng': 24.941486120224}],
     'distance': 398,
     'postalCode': '00100',
     'cc': 'FI',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Kaivokatu 1', '00100 Helsinki', 'Suomi']},
    'categories': [{'id': '4f4530164b9074f6e4fb00ff',
      'name': 'Tourist Information Center',
      'pluralName': 'Tourist Information Centers',
      'shortName': 'Tourist Information',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/touristinformation_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592653457',
    

In [106]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id  \
0  5ca2f39aea1e44002c7dccc9   
1  55e1f457498e5e9426833290   
2  4ffd6158e4b06453d659f334   
3  4adcdb23f964a520976021e3   
4  4cff88e941322d43c9a620c1   

                                                name  \
0  Helsinki Tourist Information (Helsingin matkai...   
1                 Rööperi Tourist Information Center   
2  Erilainen matkailutoimisto / Alternative Touri...   
3          Helsinki City Tourist & Convention Bureau   
4                                              Citec   

                                          categories    referralId  hasPerk  \
0  [{'id': '4f4530164b9074f6e4fb00ff', 'name': 'T...  v-1592653457    False   
1  [{'id': '4f4530164b9074f6e4fb00ff', 'name': 'T...  v-1592653457    False   
2  [{'id': '4f4530164b9074f6e4fb00ff', 'name': 'T...  v-1592653457    False   
3  [{'id': '4f4530164b9074f6e4fb00ff', 'name': 'T...  v-1592653457    False   
4  [{'id': '4bf58dd8d48988d124941735', 'name': 'O...  v-1592653457    False   

             location.address  location.lat  location.lng  \
0                 Kaivokatu 1     60.170949     24.941486   
1           Laivurinkatu 10 B     60.161101     24.941153   
2            Unioninkatu 27 B     60.168839     24.951179   
3         Pohjoisesplanadi 19     60.167804     24.950438   
4  Pohjoinen hesperiankatu 15     60.177528     24.925136   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.17094859970501...                398   
1  [{'label': 'display', 'lat': 60.16110059272716...                706   
2  [{'label': 'display', 'lat': 60.16883949993765...                502   
3  [{'label': 'display', 'lat': 60.16780408286753...                437   
4  [{'label': 'display', 'lat': 60.17752809634241...               1483   

  location.postalCode location.cc location.city location.state  \
0               00100          FI      Helsinki        Uusimaa   
1                 NaN          FI      Helsinki        Uusimaa   
2               00170          FI      Helsinki        Uusimaa   
3               00099          FI      Helsinki        Uusimaa   
4               00260          FI      Helsinki        Uusimaa   

  location.country                          location.formattedAddress  \
0            Suomi               [Kaivokatu 1, 00100 Helsinki, Suomi]   
1            Suomi               [Laivurinkatu 10 B, Helsinki, Suomi]   
2            Suomi          [Unioninkatu 27 B, 00170 Helsinki, Suomi]   
3            Suomi       [Pohjoisesplanadi 19, 00099 Helsinki, Suomi]   
4            Suomi  [Pohjoinen hesperiankatu 15 (Töölöntorinkatu),...   

  location.crossStreet  
0                  NaN  
1                  NaN  
2                  NaN  
3                  NaN  
4      Töölöntorinkatu

In [109]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
# dataframe_filtered
dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Tourist Information Center'] 
dataframe_filtered

name  \
0  Helsinki Tourist Information (Helsingin matkai...   
1                 Rööperi Tourist Information Center   
2  Erilainen matkailutoimisto / Alternative Touri...   
3          Helsinki City Tourist & Convention Bureau   

                   categories              address        lat        lng  \
0  Tourist Information Center          Kaivokatu 1  60.170949  24.941486   
1  Tourist Information Center    Laivurinkatu 10 B  60.161101  24.941153   
2  Tourist Information Center     Unioninkatu 27 B  60.168839  24.951179   
3  Tourist Information Center  Pohjoisesplanadi 19  60.167804  24.950438   

                                      labeledLatLngs  distance postalCode  cc  \
0  [{'label': 'display', 'lat': 60.17094859970501...       398      00100  FI   
1  [{'label': 'display', 'lat': 60.16110059272716...       706        NaN  FI   
2  [{'label': 'display', 'lat': 60.16883949993765...       502      00170  FI   
3  [{'label': 'display', 'lat': 60.16780408286753...       437      00099  FI   

       city    state country                              formattedAddress  \
0  Helsinki  Uusimaa   Suomi          [Kaivokatu 1, 00100 Helsinki, Suomi]   
1  Helsinki  Uusimaa   Suomi          [Laivurinkatu 10 B, Helsinki, Suomi]   
2  Helsinki  Uusimaa   Suomi     [Unioninkatu 27 B, 00170 Helsinki, Suomi]   
3  Helsinki  Uusimaa   Suomi  [Pohjoisesplanadi 19, 00099 Helsinki, Suomi]   

  crossStreet                        id  
0         NaN  5ca2f39aea1e44002c7dccc9  
1         NaN  55e1f457498e5e9426833290  
2         NaN  4ffd6158e4b06453d659f334  
3         NaN  4adcdb23f964a520976021e3

In [110]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=14) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='maroon',
        popup=label,
        fill = True,
        fill_color='black',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Search for Pub

In [51]:
# search for pubs
search_query = 'Pub'
radius = 2000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Pub&radius=2000&limit=100'

In [52]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf0acb9a389001b11c0b3'},
 'response': {'venues': [{'id': '4adcdb21f964a520fd5f21e3',
    'name': "Henry's Pub",
    'location': {'address': 'Simonkatu 3',
     'lat': 60.16981493731562,
     'lng': 24.9356596916914,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.16981493731562,
       'lng': 24.9356596916914}],
     'distance': 467,
     'postalCode': '00100',
     'cc': 'FI',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Simonkatu 3', '00100 Helsinki', 'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d14c941735',
      'name': 'Wings Joint',
      'pluralName': 'Wings Joints',
      'shortName': 'Wings',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/wings_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592652127',
    'hasPerk': False},
   {'id': '4adcdb21f964a5201c6021e3',
    'name': 'Pub Gaselli',
    'location': {'add

In [53]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                  name  \
0  4adcdb21f964a520fd5f21e3           Henry's Pub   
1  4adcdb21f964a5201c6021e3           Pub Gaselli   
2  4afd717cf964a520d92722e3          Pickwick Pub   
3  4aea087cf964a520abb821e3     Sport Pub Chelsea   
4  4d70ecfb95acb1f752eb0cb9  Kitty's Public House   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d14c941735', 'name': 'W...  v-1592652127    False   
1  [{'id': '56aa371ce4b08b9a8d57356c', 'name': 'B...  v-1592652127    False   
2  [{'id': '4bf58dd8d48988d11b941735', 'name': 'P...  v-1592652127    False   
3  [{'id': '4bf58dd8d48988d11d941735', 'name': 'S...  v-1592652127    False   
4  [{'id': '56aa371ce4b08b9a8d57356c', 'name': 'B...  v-1592652127    False   

      location.address  location.lat  location.lng  \
0          Simonkatu 3     60.169815     24.935660   
1  Aleksanterinkatu 46     60.168389     24.945144   
2         Kaivokatu 10     60.170551     24.940582   
3   Töölönlahdenkatu 1     60.172665     24.938968   
4         Keskuskatu 6     60.169495     24.941717   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.16981493731562...                467   
1  [{'label': 'display', 'lat': 60.16838890070473...                179   
2  [{'label': 'display', 'lat': 60.17055067731783...                366   
3  [{'label': 'display', 'lat': 60.17266511242318...                618   
4  [{'label': 'display', 'lat': 60.16949539149372...                237   

  location.postalCode location.cc location.city location.state  \
0               00100          FI      Helsinki        Uusimaa   
1               00100          FI      Helsinki        Uusimaa   
2               00100          FI      Helsinki        Uusimaa   
3               00100          FI      Helsinki        Uusimaa   
4               00100          FI      Helsinki        Uusimaa   

  location.country                          location.formattedAddress  \
0            Suomi               [Simonkatu 3, 00100 Helsinki, Suomi]   
1            Suomi       [Aleksanterinkatu 46, 00100 Helsinki, Suomi]   
2            Suomi  [Kaivokatu 10 (at Rautatieasema), 00100 Helsin...   
3            Suomi  [Töölönlahdenkatu 1 (Alvar Aallon Kuja), 00100...   
4            Suomi  [Keskuskatu 6 (Citykäytävä), 00100 Helsinki, S...   

  venuePage.id location.crossStreet location.neighborhood  
0          NaN                  NaN                   NaN  
1     53096432                  NaN                   NaN  
2          NaN     at Rautatieasema                   NaN  
3          NaN    Alvar Aallon Kuja                   NaN  
4     33622926          Citykäytävä                   NaN

In [54]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Pub'] 
dataframe_filtered

name categories                   address        lat  \
2             Pickwick Pub        Pub              Kaivokatu 10  60.170551   
5             Old Port Pub        Pub        M/S Silja Symphony  60.162496   
7               Pub Ludvig        Pub            Ludviginkatu 1  60.165900   
10              Pub Ikkuna        Pub             Salomonkatu 4  60.169875   
13             Pub Old Hat        Pub         Mannerheimintie 3  60.169317   
15            Merimies Pub        Pub         Merimiehenkatu 27  60.160418   
18             Pub Karumaa        Pub             Mariegatan 12  60.171101   
23                  Pub 99        Pub        Mannerheimintie 58  60.181993   
25                 Sea Pub        Pub        M/S Silja Serenade  60.161627   
27               Snadi Pub        Pub            Kolmas linja 6  60.181473   
32             Pub Seaport        Pub                       NaN  60.151796   
36                 Sea Pub        Pub  Tallink M/S Silja Europa  60.154310   
38  Hemingway's Bar & Cafe        Pub                  Aikatalo  60.169916   
42               SpåraKOFF        Pub                       NaN  60.171168   
44           Public Corner        Pub              Mikonkatu 15  60.171240   
48              Angleterre        Pub          Fredrikinkatu 47  60.166254   

          lng                                     labeledLatLngs  distance  \
2   24.940582  [{'label': 'display', 'lat': 60.17055067731783...       366   
5   24.957605  [{'label': 'display', 'lat': 60.16249550677987...       995   
7   24.945667  [{'label': 'display', 'lat': 60.1659, 'lng': 2...       239   
10  24.934033  [{'label': 'display', 'lat': 60.16987497689356...       546   
13  24.940810  [{'label': 'display', 'lat': 60.16931659999999...       233   
15  24.938362  [{'label': 'display', 'lat': 60.16041816197626...       812   
18  24.956648  [{'label': 'display', 'lat': 60.171101, 'lng':...       880   
23  24.927069  [{'label': 'display', 'lat': 60.18199269594967...      1836   
25  24.959400  [{'label': 'display', 'lat': 60.161627, 'lng':...      1132   
27  24.951012  [{'label': 'display', 'lat': 60.181473, 'lng':...      1633   
32  24.919503  [{'label': 'display', 'lat': 60.15179637808387...      2157   
36  24.922170  [{'label': 'display', 'lat': 60.15431, 'lng': ...      1845   
38  24.945187  [{'label': 'display', 'lat': 60.16991576000335...       314   
42  24.944651  [{'label': 'display', 'lat': 60.17116846959888...       433   
44  24.945610  [{'label': 'display', 'lat': 60.17124, 'lng': ...       458   
48  24.934633  [{'label': 'display', 'lat': 60.16625428697945...       458   

   postalCode  cc      city    state country  \
2       00100  FI  Helsinki  Uusimaa   Suomi   
5         NaN  FI       NaN      NaN   Suomi   
7       00130  FI  Helsinki  Uusimaa   Suomi   
10      00100  FI  Helsinki  Uusimaa   Suomi   
13      00100  FI  Helsinki  Uusimaa   Suomi   
15      00150  FI  Helsinki  Uusimaa   Suomi   
18        NaN  FI       NaN      NaN   Suomi   
23      00260  FI  Helsinki  Uusimaa   Suomi   
25        NaN  FI  Helsinki  Uusimaa   Suomi   
27      00530  FI  Helsinki  Uusimaa   Suomi   
32        NaN  FI       NaN      NaN   Suomi   
36        NaN  FI       NaN      NaN   Suomi   
38      00100  FI  Helsinki  Uusimaa   Suomi   
42      00100  FI  Helsinki  Uusimaa   Suomi   
44      00100  FI  Helsinki  Uusimaa   Suomi   
48      00100  FI  Helsinki  Uusimaa   Suomi   

                                     formattedAddress  \
2   [Kaivokatu 10 (at Rautatieasema), 00100 Helsin...   
5                         [M/S Silja Symphony, Suomi]   
7             [Ludviginkatu 1, 00130 Helsinki, Suomi]   
10             [Salomonkatu 4, 00100 Helsinki, Suomi]   
13  [Mannerheimintie 3 (Kaivopiha), 00100 Helsinki...   
15         [Merimiehenkatu 27, 00150 Helsinki, Suomi]   
18                             [Mariegatan 12, Suomi]   
23  [Mannerheimintie 58 (Ooppera), 00260 Helsinki,...   
25              [M/S Silja Serenade, H

In [56]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=14) # generate map 


for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='black',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

## Search for Transport

### Bus

In [76]:
# search for bus
search_query = 'Bus'
radius = 2000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Bus&radius=2000&limit=100'

In [77]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf47bc8cff2001b68b4b8'},
 'response': {'venues': [{'id': '4c31d9c716adc9285c27c19c',
    'name': 'Finnair City Bus',
    'location': {'crossStreet': 'Elielinaukio - Lentoasemantie',
     'lat': 60.171611127324276,
     'lng': 24.939481776821268,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.171611127324276,
       'lng': 24.939481776821268}],
     'distance': 498,
     'postalCode': '00100',
     'cc': 'FI',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Elielinaukio - Lentoasemantie',
      '00100 Helsinki',
      'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d12b951735',
      'name': 'Bus Line',
      'pluralName': 'Bus Lines',
      'shortName': 'Bus',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/busstation_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592652969',
    'hasPerk': False},
   {'id': '50825f97e4b01

In [78]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                           name  \
0  4c31d9c716adc9285c27c19c               Finnair City Bus   
1  50825f97e4b0134248db2f4f  Helsinki - St. Petersburg Bus   
2  4d404b3ec5eaa1cd7743a050                   HSL Bussi 64   
3  4ceee851f368b1f7e9ef82f7    HSL 1001/1900/1901 Erottaja   
4  4db54cc581543d71da54a735                   HSL Bussi 24   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d12b951735', 'name': 'B...  v-1592652969    False   
1  [{'id': '4bf58dd8d48988d12b951735', 'name': 'B...  v-1592652969    False   
2  [{'id': '4bf58dd8d48988d12b951735', 'name': 'B...  v-1592652969    False   
3  [{'id': '52f2ab2ebcbc57f1066b8b4f', 'name': 'B...  v-1592652969    False   
4  [{'id': '4bf58dd8d48988d12b951735', 'name': 'B...  v-1592652969    False   

            location.crossStreet  location.lat  location.lng  \
0  Elielinaukio - Lentoasemantie     60.171611     24.939482   
1                            NaN     60.169740     24.929948   
2                            NaN     60.170688     24.943149   
3                            NaN     60.167236     24.942376   
4                            NaN     60.157474     24.945358   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.17161112732427...                498   
1  [{'label': 'display', 'lat': 60.16974016442013...                745   
2  [{'label': 'display', 'lat': 60.17068816881409...                366   
3  [{'label': 'display', 'lat': 60.16723631535787...                 22   
4  [{'label': 'display', 'lat': 60.15747357327081...               1116   

  location.postalCode location.cc location.city location.state  \
0               00100          FI      Helsinki        Uusimaa   
1                 NaN          FI      Helsinki        Uusimaa   
2                 NaN          FI      Helsinki        Uusimaa   
3               00100          FI      Helsinki        Uusimaa   
4                 NaN          FI      Helsinki        Uusimaa   

  location.country                          location.formattedAddress  \
0            Suomi  [Elielinaukio - Lentoasemantie, 00100 Helsinki...   
1            Suomi                                  [Helsinki, Suomi]   
2            Suomi      [Rautatientori - Itä-Pakila, Helsinki, Suomi]   
3            Suomi                  [Erottaja, 00100 Helsinki, Suomi]   
4            Suomi           [Merikatu - Seurasaari, Helsinki, Suomi]   

             location.address location.neighborhood  
0                         NaN                   NaN  
1                         NaN                   NaN  
2  Rautatientori - Itä-Pakila                   NaN  
3                    Erottaja                   NaN  
4       Merikatu - Seurasaari                   NaN

In [82]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
# dataframe_filtered
dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Bus Line'] 
dataframe_filtered

name categories  \
0                                    Finnair City Bus   Bus Line   
1                       Helsinki - St. Petersburg Bus   Bus Line   
2                                        HSL Bussi 64   Bus Line   
4                                        HSL Bussi 24   Bus Line   
5                                 Bussi 840 (U-linja)   Bus Line   
7                                HSL Bussi 651 / 651A   Bus Line   
8                                        HSL Bussi 14   Bus Line   
9                                        HSL Bussi 18   Bus Line   
10                                       HSL Bussi 75   Bus Line   
11                                     HSL Bussi 620N   Bus Line   
12                                       HSL Bussi 4X   Bus Line   
13                           HSL Bussi 870  (U-linja)   Bus Line   
14                                     HSL Bussi 300N   Bus Line   
15                                      Vihti ski bus   Bus Line   
16                           HSL Bussi 110/110A/110TA   Bus Line   
17  Porvoon Liikenne bussi U-linja 776 Helsinki-Ni...   Bus Line   
18                                      HSL Bussi 85N   Bus Line   
20                                      HSL Bussi 431   Bus Line   
21                                       HSL Bussi 41   Bus Line   
22                          Express Bus Hki- Virojoki   Bus Line   
23                                     HSL Bussi 143T   Bus Line   
25                      Express Bus Helsinki - Virrat   Bus Line   
26                                       HSL Bussi 40   Bus Line   
27                                       HSL Bussi 42   Bus Line   
28                                NESU Conference Bus   Bus Line   
30                     Express Bus Helsinki-Rovaniemi   Bus Line   
31                                        HSL bus 300   Bus Line   
32                                      HSL Bussi 415   Bus Line   
33                                       HSL Bussi 16   Bus Line   
34                                       HSL Bussi 63   Bus Line   
35                                       HSL Bussi 20   Bus Line   
38                                      HSL Bussi 92N   Bus Line   
40                                       HSL Bussi 73   Bus Line   
41                                       HSL Bussi 67   Bus Line   
42                                       HSL Bussi 37   Bus Line   
43                                      HSL Bussi 486   Bus Line   
44                                       HSL Bussi 39   Bus Line   
48                                       HSL Bussi 99   Bus Line   
49                                      HSL Bussi 96N   Bus Line   

                                        crossStreet        lat        lng  \
0                     Elielinaukio - Lentoasemantie  60.171611  24.939482   
1                                               NaN  60.169740  24.929948   
2                                               NaN  60.170688  24.943149   
4                                               NaN  60.157474  24.945358   
5                        Helsinki-Söderkulla-Porvoo  60.169811  24.934256   
7        Rautatientori - Tuupakka - (Viinikanmetsä)  60.171211  24.943922   
8                                               NaN  60.168352  24.931263   
9                       Eira - Kamppi - Munkkivuori  60.166352  24.930850   
10                                              NaN  60.171343  24.942758   
11            Rautatientori - Tammisto - Lentoasema  60.171211  24.942870   
12                         Kauppatori - Katajanokka  60.167550  24.951812   
13       Helsinki-Söderkulla-Porvoo-Loviisa(-Kotka)  60.169826  24.934328   
14      Eliel - Pitsku - Pähkinär - Hämeenk - Rajat  60.172118  24.939523   
15                                              NaN  60.171206  24.943946   
16         Kamppi - Lauttasaari - Mankkaa - Mäkkylä  60.169281  24.932288   
17                          Helsinki-Nikkilä-Porvoo  60.169811  24.934302   
18                 

In [83]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=15) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='purple',
        popup=label,
        fill = True,
        fill_color='black',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

### Train 

In [84]:
# search for hmetro line 
search_query = 'Metro'
radius = 3000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Metro&radius=3000&limit=100'

In [85]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf510be61c9001c720de7'},
 'response': {'venues': [{'id': '4b7e93ddf964a520a0f32fe3',
    'name': 'Metro Rautatientori',
    'location': {'address': 'Rautatieasema',
     'crossStreet': 'Kaivokatu',
     'lat': 60.17055401906809,
     'lng': 24.94035913050315,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.17055401906809,
       'lng': 24.94035913050315}],
     'distance': 370,
     'postalCode': '00100',
     'cc': 'FI',
     'city': 'Helsinki',
     'country': 'Suomi',
     'formattedAddress': ['Rautatieasema (Kaivokatu)',
      '00100 Helsinki',
      'Suomi']},
    'categories': [{'id': '4bf58dd8d48988d1fd931735',
      'name': 'Metro Station',
      'pluralName': 'Metro Stations',
      'shortName': 'Metro',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/subway_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592653073',
    'hasPerk': False},
   {'id': '4b583eb2f964a520724f28

In [86]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                       name  \
0  4b7e93ddf964a520a0f32fe3        Metro Rautatientori   
1  4b583eb2f964a520724f28e3               Metro Kamppi   
2  4b4f4439f964a52035ff26e3  Metro Helsingin yliopisto   
3  4b583fc9f964a5208f4f28e3           Metro Ruoholahti   
4  4b4f5913f964a520770227e3            Metro Hakaniemi   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d1fd931735', 'name': 'M...  v-1592653073    False   
1  [{'id': '4bf58dd8d48988d1fd931735', 'name': 'M...  v-1592653073    False   
2  [{'id': '4bf58dd8d48988d1fd931735', 'name': 'M...  v-1592653073    False   
3  [{'id': '4bf58dd8d48988d1fd931735', 'name': 'M...  v-1592653073    False   
4  [{'id': '4bf58dd8d48988d1fd931735', 'name': 'M...  v-1592653073    False   

  location.address location.crossStreet  location.lat  location.lng  \
0    Rautatieasema            Kaivokatu     60.170554     24.940359   
1     Kampinkuja 1        Fredrikinkatu     60.168630     24.930053   
2     Vuorikatu 12           Kaisaniemi     60.171718     24.947526   
3  Itämerenkatu 14                  NaN     60.163181     24.915004   
4  Porthaninkatu 2                  NaN     60.181293     24.949674   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.17055401906809...                370   
1  [{'label': 'display', 'lat': 60.16863024117757...                706   
2  [{'label': 'display', 'lat': 60.17171772601244...                552   
3  [{'label': 'display', 'lat': 60.16318090010349...               1597   
4  [{'label': 'display', 'lat': 60.1812930267338,...               1594   

  location.postalCode location.cc location.city location.country  \
0               00100          FI      Helsinki            Suomi   
1               00100          FI      Helsinki            Suomi   
2               00100          FI      Helsinki            Suomi   
3               00180          FI      Helsinki            Suomi   
4               00530          FI      Helsinki            Suomi   

                           location.formattedAddress location.state  \
0  [Rautatieasema (Kaivokatu), 00100 Helsinki, Su...            NaN   
1  [Kampinkuja 1 (Fredrikinkatu), 00100 Helsinki,...        Uusimaa   
2  [Vuorikatu 12 (Kaisaniemi), 00100 Helsinki, Su...        Uusimaa   
3           [Itämerenkatu 14, 00180 Helsinki, Suomi]        Uusimaa   
4           [Porthaninkatu 2, 00530 Helsinki, Suomi]        Uusimaa   

  location.neighborhood  
0                   NaN  
1                   NaN  
2                Kluuvi  
3                   NaN  
4                   NaN

In [87]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
# dataframe_filtered
dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Metro Station'] 
dataframe_filtered

name     categories  \
0         Metro Rautatientori  Metro Station   
1                Metro Kamppi  Metro Station   
2   Metro Helsingin yliopisto  Metro Station   
3            Metro Ruoholahti  Metro Station   
4             Metro Hakaniemi  Metro Station   
5             Metro Sörnäinen  Metro Station   
8            Metro Kalasatama  Metro Station   
9           HSL Metrolinja M1  Metro Station   
42          HSL Metrolinja M2  Metro Station   

                              address    crossStreet        lat        lng  \
0                       Rautatieasema      Kaivokatu  60.170554  24.940359   
1                        Kampinkuja 1  Fredrikinkatu  60.168630  24.930053   
2                        Vuorikatu 12     Kaisaniemi  60.171718  24.947526   
3                     Itämerenkatu 14            NaN  60.163181  24.915004   
4                     Porthaninkatu 2            NaN  60.181293  24.949674   
5                        Hämeentie 50            NaN  60.187778  24.960867   
8                Hermannin Rantatie 2            NaN  60.187323  24.977713   
9   Matinkylä - Ruoholahti - Vuosaari            NaN  60.168624  24.930083   
42               Tapiola - Mellunmäki            NaN  60.187515  24.977166   

                                       labeledLatLngs  distance postalCode  \
0   [{'label': 'display', 'lat': 60.17055401906809...       370      00100   
1   [{'label': 'display', 'lat': 60.16863024117757...       706      00100   
2   [{'label': 'display', 'lat': 60.17171772601244...       552      00100   
3   [{'label': 'display', 'lat': 60.16318090010349...      1597      00180   
4   [{'label': 'display', 'lat': 60.1812930267338,...      1594      00530   
5   [{'label': 'display', 'lat': 60.18777837850253...      2483      00500   
8   [{'label': 'display', 'lat': 60.187323, 'lng':...      2949      00580   
9   [{'label': 'display', 'lat': 60.16862429280016...       704        NaN   
42  [{'label': 'display', 'lat': 60.18751511934491...      2945        NaN   

    cc      city country                                   formattedAddress  \
0   FI  Helsinki   Suomi  [Rautatieasema (Kaivokatu), 00100 Helsinki, Su...   
1   FI  Helsinki   Suomi  [Kampinkuja 1 (Fredrikinkatu), 00100 Helsinki,...   
2   FI  Helsinki   Suomi  [Vuorikatu 12 (Kaisaniemi), 00100 Helsinki, Su...   
3   FI  Helsinki   Suomi           [Itämerenkatu 14, 00180 Helsinki, Suomi]   
4   FI  Helsinki   Suomi           [Porthaninkatu 2, 00530 Helsinki, Suomi]   
5   FI  Helsinki   Suomi              [Hämeentie 50, 00500 Helsinki, Suomi]   
8   FI  Helsinki   Suomi      [Hermannin Rantatie 2, 00580 Helsinki, Suomi]   
9   FI  Helsinki   Suomi  [Matinkylä - Ruoholahti - Vuosaari, Helsinki, ...   
42  FI  Helsinki   Suomi            [Tapiola - Mellunmäki, Helsinki, Suomi]   

      state neighborhood                        id  
0       NaN          NaN  4b7e93ddf964a520a0f32fe3  
1   Uusimaa          NaN  4b583eb2f964a520724f28e3  
2   Uusimaa       Kluuvi  4b4f4439f964a52035ff26e3  
3   Uusimaa          NaN  4b583fc9f964a5208f4f28e3  
4   Uusimaa          NaN  4b4f5913f964a520770227e3  
5   Uusimaa          NaN  4b42d3faf964a5203fda25e3  
8   Uusimaa          NaN  4b7e6348f964a5201ceb2fe3  
9   Uusimaa          NaN  57b5b22e498ebc73ed4ec627  
42  Uusimaa          NaN  57b5b335498ecbd36bd6bee5

In [88]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=13) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='black',
        popup=label,
        fill = True,
        fill_color='orange',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

### Ferry and Boat

In [89]:
# search for boat
search_query = 'Boat'
radius = 3000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Boat&radius=3000&limit=100'

In [90]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf4dcd03993001c02143b'},
 'response': {'venues': [{'id': '5c6ed0a7180b91003ab7636a',
    'name': 'Hotel Boat Isosaari',
    'location': {'lat': 60.166546,
     'lng': 24.958786,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.166546,
       'lng': 24.958786}],
     'distance': 902,
     'cc': 'FI',
     'country': 'Suomi',
     'formattedAddress': ['Suomi']},
    'categories': [{'id': '4bf58dd8d48988d1fa931735',
      'name': 'Hotel',
      'pluralName': 'Hotels',
      'shortName': 'Hotel',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/travel/hotel_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592653159',
    'hasPerk': False},
   {'id': '594d1e19bed48303ebb91c15',
    'name': 'White Sand Boat',
    'location': {'address': 'Sillilaituri',
     'lat': 60.161825,
     'lng': 24.922822,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.161825,
       'lng': 24.922822}],
    

In [91]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                 name  \
0  5c6ed0a7180b91003ab7636a  Hotel Boat Isosaari   
1  594d1e19bed48303ebb91c15      White Sand Boat   
2  51e812ec498e1e4d8e0fdc47            Love Boat   
3  4ced1ba58604a1cd5167f0c0    Boat Of Rajasaari   
4  51eff1e5498e72e70d1a11a1          Särkkä Boat   

                                          categories    referralId  hasPerk  \
0  [{'id': '4bf58dd8d48988d1fa931735', 'name': 'H...  v-1592653159    False   
1  [{'id': '5744ccdfe4b0c0459246b4c1', 'name': 'B...  v-1592653159    False   
2  [{'id': '4bf58dd8d48988d11a941735', 'name': 'O...  v-1592653159    False   
3  [{'id': '4bf58dd8d48988d12d951735', 'name': 'B...  v-1592653159    False   
4  [{'id': '4bf58dd8d48988d12d951735', 'name': 'B...  v-1592653159    False   

   location.lat  location.lng  \
0     60.166546     24.958786   
1     60.161825     24.922822   
2     60.154001     24.960421   
3     60.182617     24.909935   
4     60.151944     24.965753   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.166546, 'lng':...                902   
1  [{'label': 'display', 'lat': 60.161825, 'lng':...               1258   
2  [{'label': 'display', 'lat': 60.15400066545896...               1790   
3  [{'label': 'display', 'lat': 60.18261702805189...               2476   
4  [{'label': 'display', 'lat': 60.15194389945159...               2147   

  location.cc location.country              location.formattedAddress  \
0          FI            Suomi                                [Suomi]   
1          FI            Suomi  [Sillilaituri, 00180 Helsinki, Suomi]   
2          FI            Suomi                                [Suomi]   
3          FI            Suomi                                [Suomi]   
4          FI            Suomi                                [Suomi]   

  location.address location.postalCode location.city location.state  \
0              NaN                 NaN           NaN            NaN   
1     Sillilaituri               00180      Helsinki        Uusimaa   
2              NaN                 NaN           NaN            NaN   
3              NaN                 NaN           NaN            NaN   
4              NaN                 NaN           NaN            NaN   

  location.crossStreet  
0                  NaN  
1                  NaN  
2                  NaN  
3                  NaN  
4                  NaN

In [92]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
# dataframe_filtered
dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Boat or Ferry'] 
dataframe_filtered

name     categories        lat        lng  \
3    Boat Of Rajasaari  Boat or Ferry  60.182617  24.909935   
4          Särkkä Boat  Boat or Ferry  60.151944  24.965753   
5  Royal Line m/s King  Boat or Ferry  60.167399  24.953591   
6    Uunisaaren lautta  Boat or Ferry  60.155170  24.950434   

                                      labeledLatLngs  distance  cc country  \
3  [{'label': 'display', 'lat': 60.18261702805189...      2476  FI   Suomi   
4  [{'label': 'display', 'lat': 60.15194389945159...      2147  FI   Suomi   
5  [{'label': 'display', 'lat': 60.16739897397452...       609  FI   Suomi   
6  [{'label': 'display', 'lat': 60.15517019753707...      1430  FI   Suomi   

                                  formattedAddress     address postalCode  \
3                                          [Suomi]         NaN        NaN   
4                                          [Suomi]         NaN        NaN   
5  [Kauppatori (Esplanadi), 00130 Helsinki, Suomi]  Kauppatori      00130   
6      [Kompassitori - Uunisaari, Helsinki, Suomi]         NaN        NaN   

       city    state               crossStreet                        id  
3       NaN      NaN                       NaN  4ced1ba58604a1cd5167f0c0  
4       NaN      NaN                       NaN  51eff1e5498e72e70d1a11a1  
5  Helsinki  Uusimaa                 Esplanadi  4c3dc6d3a9509c74cca2395b  
6  Helsinki  Uusimaa  Kompassitori - Uunisaari  4c63fe7b86b6be9a7bd88f34

In [93]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=13) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='black',
        popup=label,
        fill = True,
        fill_color='orange',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

In [70]:
# search for park
search_query = 'Park'
radius = 2000

# Define the corresponding URL
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'\
.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=U23ZJ052IZMG1VQ1NIKMKCA10CAMY0THT24RHNEDBQIBWVU3&client_secret=P5DS0JQQSV4JL1IKJAJZ0LDLXEHREDRIXRPNYC4LAHWFYFPU&ll=60.1674098,24.9425769&v=20180605&query=Park&radius=2000&limit=100'

In [71]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5eedf1c5ed78b8001b08dedf'},
 'response': {'venues': [{'id': '4bcae64e68f976b03c216083',
    'name': 'Q-Park Stockmann',
    'location': {'address': 'Aleksanterinkatu 52',
     'crossStreet': 'Mannerheimintie 10',
     'lat': 60.168365974244665,
     'lng': 24.94110582061266,
     'labeledLatLngs': [{'label': 'display',
       'lat': 60.168365974244665,
       'lng': 24.94110582061266}],
     'distance': 134,
     'postalCode': '00100',
     'cc': 'FI',
     'city': 'Helsinki',
     'state': 'Uusimaa',
     'country': 'Suomi',
     'formattedAddress': ['Aleksanterinkatu 52 (Mannerheimintie 10)',
      '00100 Helsinki',
      'Suomi']},
    'categories': [{'id': '4c38df4de52ce0d596b336e1',
      'name': 'Parking',
      'pluralName': 'Parking',
      'shortName': 'Parking',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/building/parking_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1592652443',
    'hasPe

In [72]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
dataframe = json_normalize(venues)
dataframe.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:5: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  """


id                   name  \
0  4bcae64e68f976b03c216083       Q-Park Stockmann   
1  4c99a8bedb10b60c38168c6d                 Q-Park   
2  4d3e86ff8edf37044a9cc4a5  Business Meeting Park   
3  51213ff8e4b0d82e65ed892d     Q-Park Kasarmitori   
4  4d8205ea21c0b60c9bc7e46f                 Q-Park   

                                          categories    referralId  hasPerk  \
0  [{'id': '4c38df4de52ce0d596b336e1', 'name': 'P...  v-1592652443    False   
1  [{'id': '4c38df4de52ce0d596b336e1', 'name': 'P...  v-1592652443    False   
2  [{'id': '4bf58dd8d48988d100941735', 'name': 'M...  v-1592652443    False   
3  [{'id': '4c38df4de52ce0d596b336e1', 'name': 'P...  v-1592652443    False   
4  [{'id': '4c38df4de52ce0d596b336e1', 'name': 'P...  v-1592652443    False   

       location.address location.crossStreet  location.lat  location.lng  \
0   Aleksanterinkatu 52   Mannerheimintie 10     60.168366     24.941106   
1        Yrjönkatu 8-10                  NaN     60.166395     24.942677   
2  Mannerheimintie 20 B                  NaN     60.169254     24.938035   
3       Fabianinkatu 17                  NaN     60.165249     24.949189   
4       Fabianinkatu 17                  NaN     60.164905     24.947899   

                             location.labeledLatLngs  location.distance  \
0  [{'label': 'display', 'lat': 60.16836597424466...                134   
1  [{'label': 'display', 'lat': 60.16639459960963...                113   
2  [{'label': 'display', 'lat': 60.16925402376697...                324   
3  [{'label': 'display', 'lat': 60.16524942826466...                438   
4  [{'label': 'display', 'lat': 60.16490498812899...                405   

  location.postalCode location.cc location.city    location.state  \
0               00100          FI      Helsinki           Uusimaa   
1               00120          FI      Helsinki           Uusimaa   
2               00100          FI      Helsinki           Uusimaa   
3               00130          FI      Helsinki           Uusimaa   
4               00130          FI      Helsinki  Southern Finland   

  location.country                          location.formattedAddress  \
0            Suomi  [Aleksanterinkatu 52 (Mannerheimintie 10), 001...   
1            Suomi            [Yrjönkatu 8-10, 00120 Helsinki, Suomi]   
2            Suomi      [Mannerheimintie 20 B, 00100 Helsinki, Suomi]   
3            Suomi           [Fabianinkatu 17, 00130 Helsinki, Suomi]   
4            Suomi           [Fabianinkatu 17, 00130 Helsinki, Suomi]   

  venuePage.id  location.neighborhood  
0          NaN                    NaN  
1          NaN                    NaN  
2     52955886                    NaN  
3          NaN                    NaN  
4          NaN  Kaartinkaup, Helsinki

In [73]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]
# dataframe_filtered
dataframe_filtered = dataframe_filtered.loc[dataframe_filtered['categories'] == 'Park'] 
dataframe_filtered

name categories           address  \
11                         Esplanadin puisto       Park    Eteläesplanadi   
19                                Fanny Park       Park               NaN   
24                       Kristuskyrkans Park       Park               NaN   
26                     Sinebrychoffin puisto       Park      Bulevardi 40   
28                           Tähtitorninmäki       Park   Tähtitorninkatu   
29  Kaivopuisto / Brunnsparken (Kaivopuisto)       Park               NaN   
33                        Kaisaniemen puisto       Park        Kaisaniemi   
46                           Finlandiapuisto       Park  Karamzininkatu 2   

         crossStreet        lat        lng  \
11  Pohjoisesplanadi  60.167498  24.947035   
19               NaN  60.162028  24.933010   
24               NaN  60.175857  24.949225   
26               NaN  60.161625  24.933676   
28       Unioninkatu  60.161977  24.952762   
29               NaN  60.156810  24.956732   
33       Unioninkatu  60.173984  24.944164   
46               NaN  60.175458  24.936581   

                                       labeledLatLngs  distance postalCode  \
11                                                NaN       247      00100   
19  [{'label': 'display', 'lat': 60.162028, 'lng':...       799        NaN   
24  [{'label': 'display', 'lat': 60.17585732845229...      1009        NaN   
26  [{'label': 'display', 'lat': 60.16162517793622...       810      00180   
28  [{'label': 'display', 'lat': 60.16197749636095...       826      00140   
29  [{'label': 'display', 'lat': 60.15680978091396...      1416      00140   
33  [{'label': 'display', 'lat': 60.17398389674315...       737      00100   
46  [{'label': 'display', 'lat': 60.175458, 'lng':...       955        NaN   

    cc      city    state country  \
11  FI  Helsinki  Uusimaa   Suomi   
19  FI       NaN      NaN   Suomi   
24  FI       NaN      NaN   Suomi   
26  FI  Helsinki  Uusimaa   Suomi   
28  FI  Helsinki  Uusimaa   Suomi   
29  FI  Helsinki  Uusimaa   Suomi   
33  FI  Helsinki  Uusimaa   Suomi   
46  FI  Helsinki  Uusimaa   Suomi   

                                     formattedAddress neighborhood  \
11  [Eteläesplanadi (Pohjoisesplanadi), 00100 Hels...          NaN   
19                                            [Suomi]          NaN   
24                                            [Suomi]          NaN   
26              [Bulevardi 40, 00180 Helsinki, Suomi]          NaN   
28  [Tähtitorninkatu (Unioninkatu), 00140 Helsinki...          NaN   
29               [Kaivopuisto, 00140 Helsinki, Suomi]          NaN   
33  [Kaisaniemi (Unioninkatu), 00100 Helsinki, Suomi]          NaN   
46                [Karamzininkatu 2, Helsinki, Suomi]          NaN   

                          id  
11  4baf5d61f964a5207ffa3be3  
19  51ea5ee7498e9a0666f3e406  
24  50114463e4b05d9dc702f68e  
26  4b5abb30f964a52061d228e3  
28  4ba8f64ef964a5202dfe39e3  
29  4adcdb22f964a520826021e3  
33  4adcdb22f964a520676021e3  
46  4adcdb23f964a5209c6021e3

In [75]:
venues_map = folium.Map(location=[latitude, longitude], zoom_start=14) # generate map 

for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='black',
        popup=label,
        fill = True,
        fill_color='orange',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map